In [1]:
import numpy as np
import matplotlib.pyplot as plt
import csv
import numpy.linalg as LA
import random
import pandas as pd
from numpy import inf
import torch
from torch import nn
import matplotlib
matplotlib.use('Agg')
import matplotlib.pyplot as plt
import torch.optim as optim
import json
import itertools
import math
import pyprind
from random import sample

In [2]:
#f = open('data_irl_model/Feb23_data_exploratory_policy.json')
f = open('data_irl_model/Feb22_dataSVO.json')
data_irl = json.load(f)

In [3]:
data_keys=list(data_irl.keys())
data_keys.sort()

keys_for_training=[]
keys_for_testing=[]

index=0
for vehicle in data_keys:
    if index%10==0:
        keys_for_testing.append(vehicle)
        index+=1
    else:
        keys_for_training.append(vehicle)
        index+=1

In [4]:
len(keys_for_training)

5400

In [ ]:
data_irl[str(keys_for_testing[10])]

In [61]:
time_step=5
[data_irl[str(keys_for_testing[0])][0],data_irl[str(keys_for_testing[0])][1]]#[:][time_step]

input_tens=torch.empty(len(data_irl[str(keys_for_testing[0])]),dtype=torch.float)#.to_device(self.device)
for i in range(len(data_irl[str(keys_for_testing[0])])):
    torch.cat((input_tens,torch.tensor(data_irl[str(keys_for_testing[0])][i][time_step])))

print(input_tens)

RuntimeError: zero-dimensional tensor (at position 1) cannot be concatenated

In [79]:
a123=np.array(data_irl[str(keys_for_testing[0])])
float_arr = np.vstack(a123[:, :]).astype(np.float)
#float_arr = np.vstack(a123[:, time_step]).astype(np.float)
#input=torch.tensor(float_arr,dtype=torch.float)
#input



C:\Users\nish\AppData\Local\Temp/ipykernel_15496/2787279764.py:2: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  float_arr = np.vstack(a123[:, time_step]).astype(np.float)


tensor([[-41.2827],
        [-48.9769],
        [  8.9757],
        [  6.6194],
        [  1.1115],
        [ -1.5041]])

In [185]:
#########################################################################
################################ AIS_gen ################################

################################ Model 1 ################################ 

class GenerateAis1(nn.Module):

    #def __init__(self,n_input,n_state,n_psi2_in=64,n_psi2_out=128):
    def __init__(self,n_input,n_state,n_psi2_in=8,n_psi2_out=16):
        super(GenerateAis1,self).__init__()
        self.PSI_layer1=nn.Linear(n_input,n_psi2_in)     # Use RELU after
        self.PSI_layer2=nn.Linear(n_psi2_in,n_psi2_out)      # Use RELU after
        self.PSI_layer3=nn.GRUCell(n_psi2_out,n_state)       # This is the Gated layer

    def forward(self,x,h):
        #x=torch.transpose(x,0,1)
        #h=torch.transpose(h,0,1)
        x=torch.relu(self.PSI_layer1(x))
        x=torch.relu(self.PSI_layer2(x))
        h=self.PSI_layer3(x,h)
        return h 
    
################################ Model 2 ################################ 

class GenerateAis2(nn.Module):

    #def __init__(self,n_input,n_state,n_psi2_in=64,n_psi2_out=128):
    def __init__(self,n_input,n_state_enc,n_psi1_out=8):
        super(GenerateAis2,self).__init__()
        self.PSI_layer1=nn.Linear(n_input,n_psi1_out)     # Use RELU after
        self.PSI_layer2=nn.GRUCell(n_psi1_out,n_state_enc)       # This is the Gated layer

    def forward(self,x,h):
        #x=torch.transpose(x,0,1)
        #h=torch.transpose(h,0,1)
        #x=torch.relu(self.PSI_layer1(x))
        x=torch.relu(self.PSI_layer1(x))
        h=self.PSI_layer2(x,h)
        return h 

class GenerateAis2_LSTM(nn.Module):

    def __init__(self, n_input, n_state_enc, n_psi1_out=8):
        super(GenerateAis2_LSTM, self).__init__()
        self.PSI_layer1 = nn.Linear(n_input, n_psi1_out)  # Use RELU after
        self.PSI_layer2 = nn.LSTMCell(n_psi1_out, n_state_enc)  # LSTMCell instead of GRUCell

    def forward(self, x, h, c):
        print("Encoder Forward")
        x = torch.relu(self.PSI_layer1(x))
        h, c = self.PSI_layer2(x, (h, c))  # LSTMCell returns both new hidden state (h) and cell state (c)
        return h, c
    
class GenerateAis_GRUShallow(nn.Module):

    #def __init__(self,n_input,n_state,n_psi2_in=64,n_psi2_out=128):
    def __init__(self,n_input,n_state_enc):
        super(GenerateAis_GRUShallow,self).__init__()
        self.PSI_layer1=nn.GRUCell(n_input,n_state_enc)       # This is the Gated layer

    def forward(self,x,h):
        h=self.PSI_layer1(x,h)
        return h 

class GenerateAis_LSTMShallow(nn.Module):

    def __init__(self, n_input, n_state_enc):
        super(GenerateAis_LSTMShallow, self).__init__()
        self.PSI_layer1 = nn.LSTMCell(n_input, n_state_enc)  # LSTMCell instead of GRUCell

    def forward(self, x, h, c):
        print("Encoder Forward")
        h, c = self.PSI_layer1(x, (h, c))  # LSTMCell returns both new hidden state (h) and cell state (c)
        return h, c

In [188]:
#########################################################################
################################ AIS_pred ###############################

################################ Model 1 ################################ 

class PredictAis1(nn.Module):
    
    #def __init__(self,n_output,n_state,n_phi2_in=16,n_phi2_out=8):
    def __init__(self,n_output,n_state,n_phi2_in=2,n_phi2_out=4):
        super(PredictAis1,self).__init__()
        self.PHI_layer1=nn.Linear(n_state,n_phi2_in)  # Use RELU after
        self.PHI_layer2=nn.Linear(n_phi2_in,n_phi2_out)     # Use RELU after
        self.PHI_layer3=nn.Linear(n_phi2_out,n_output)         # mean vector of a unit-variance multivariate Gaussian distribution, samples from which are used to predict the next observation

    def forward(self,x):
        x=torch.relu(self.PHI_layer1(x))
        x=torch.relu(self.PHI_layer2(x))
        output=self.PHI_layer3(x)
        return output


################################ Model 2 - RNN based ################################ 

class PredictAis2(nn.Module):
    
    #def __init__(self,n_output,n_state,n_phi2_in=16,n_phi2_out=8):
    def __init__(self,n_output,n_input_dec,n_state_dec):
        super(PredictAis2,self).__init__()
        #self.PHI_layer1=nn.Linear(n_output,n_state_enc)  # Use RELU after
        self.PHI_layer2=nn.GRUCell(n_input_dec,n_state_dec)       # This is the Gated layer - n_state_enc+1 for time step as input
        self.PHI_layer3=nn.Linear(n_state_dec,n_output)         # mean vector of a unit-variance multivariate Gaussian distribution, samples from which are used to predict the next observation

    def forward(self,x,h):        
        #x=self.PHI_layer1(x)   
        h=self.PHI_layer2(x,h)
        #input_layer3=torch.relu(h)
        #output=-torch.relu(self.PHI_layer3(h))
        output=self.PHI_layer3(h)
        return output,h

class PredictAis_GRUSHallow(nn.Module):
    
    #def __init__(self,n_output,n_state,n_phi2_in=16,n_phi2_out=8):
    def __init__(self,n_input_dec,n_state_dec): #n_output=n_state_dec
        super(PredictAis_GRUSHallow,self).__init__()
        self.PHI_layer1=nn.GRUCell(n_input_dec,n_state_dec)       # This is the Gated layer - n_state_enc+1 for time step as input
    
    def forward(self,x,h):        
        h=self.PHI_layer1(x,h)
        return h

class PredictAis2_LSTM(nn.Module):
    
    def __init__(self, n_output, n_input_dec, n_state_dec):
        super(PredictAis2_LSTM, self).__init__()        
        #self.encoder = nn.Linear(n_output, n_input_dec)
        self.PHI_layer2 = nn.LSTMCell(n_input_dec, n_state_dec)
        self.PHI_layer3 = nn.Linear(n_state_dec, n_output)
        
    def forward(self, x, h, c):
        h, c = self.PHI_layer2(x, (h, c))
        output = self.PHI_layer3(h)
        return output, h, c
    
class PredictAis_LSTMShallow(nn.Module):
    
    def __init__(self,n_input_dec, n_state_dec):#n_output=n_state_dec
        super(PredictAis_LSTMShallow, self).__init__()        
        self.PHI_layer1 = nn.LSTMCell(n_input_dec, n_state_dec)

        
    def forward(self, x, h, c):
        h, c = self.PHI_layer1(x, (h, c))
        return h, c

In [7]:
negative_vals=[]
for i in [0,1]:
    negative_vals.append(list(filter(lambda x: x < 1, data_irl[str(keys_for_testing[0])][i])))
print(negative_vals)

[[-50.0, -48.1, -46.4, -44.761122658207675, -43.05127992142175, -41.28274312577878, -39.46536936838444, -37.60696288521823, -35.71356531742613, -33.78968838023041, -31.838501427503736, -29.861986078108643, -27.861070285758846, -25.835754674634355, -23.785244071125202, -21.708096136013104, -19.60239595060883, -17.4659597386202, -15.29656284320157, -13.092178062307937, -10.851202938627893, -8.573166165623306, -6.259465148147179, -3.913311880225578, -1.5399957277141993, 0.8524037569850123], [-56.30088862147648, -54.726865665496135, -53.206261143616395, -51.740175800649745, -50.32985055901144, -48.97686996364336, -47.68307154610725, -46.450560206681246, -45.281725232740015, -44.17925946401058, -43.1461798219091, -42.18584795159752, -41.30198901475314, -40.49870563862401, -39.7804825945506, -39.15217590591451, -38.61897783980735, -38.186346917018525, -37.85989037368617, -37.64518666049085, -37.54753932832985, -37.528616713070534, -37.528616713070534, -37.528616713070534, -37.528616713070534

In [193]:
class NN_structure(object):
    def __init__(self,n_epochs,min_timesteps,n_rollout,n_test,n_input,n_output,n_state_enc,n_state_dec,learning_rate,ais_gen_model,ais_pred_model,device):
        self.n_epochs=n_epochs
        self.min_timesteps=min_timesteps
        self.rollout=n_rollout
        self.n_test=n_test
        self.n_input=n_input
        self.n_output=n_output
        self.n_state_enc=n_state_enc    # Hidden state size in RNN
        self.n_state_dec=n_state_dec
        self.learning_rate=learning_rate                
        self.device=device
        self.ais_gen_model=ais_gen_model
        self.ais_pred_model=ais_pred_model

        self.n_psi2_in=8
        self.n_psi2_out=16
        self.n_phi2_in=2
        self.n_phi2_out=4
        self.n_psi1_out=8
        
        if ais_gen_model==1:
            self.gen_model=GenerateAis1(self.n_input,self.n_state_enc,self.n_psi2_in,self.n_psi2_out).to(self.device)      
        
        if ais_gen_model==2: 
            #self.gen_model=GenerateAis2(self.n_input,self.n_state_enc,self.n_psi1_out).to(self.device)        
            #self.gen_model=GenerateAis2_LSTM(self.n_input,self.n_state_enc,self.n_psi1_out).to(self.device)
            self.gen_model=GenerateAis_LSTMShallow(self.n_input,self.n_state_enc).to(self.device)  

        if ais_pred_model==1:
            self.pred_model=PredictAis1(self.n_output,self.n_state_enc,self.n_phi2_in,self.n_phi2_out).to(self.device)
        
        if ais_pred_model==2:
            #self.pred_model=PredictAis2(self.n_output,self.n_state_enc+1,self.n_state_dec).to(self.device)
            #self.pred_model=PredictAis2_LSTM(self.n_output,self.n_state_enc+1,self.n_state_dec).to(self.device)
            self.pred_model=PredictAis_LSTMShallow(self.n_state_enc+1,self.n_state_dec).to(self.device)

    def save_model_weights(self,text="_"):
        #name_gen_path="trained_models/IRL_based_models/IRL_SVOpolicy_ais_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+text+".pth"
        #torch.save(self.gen_model.state_dict(),name_gen_path)
        
        name_gen_path="_"
        name_pred_path="_"
        if self.ais_pred_model==1:
            name_pred_path="trained_models/IRL_based_models/IRL_SVOpolicy_ais_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+text+".pth"
            name_gen_path="trained_models/IRL_based_models/IRL_SVOpolicy_ais_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+text+".pth"

        if self.ais_pred_model==2:
            name_pred_path="trained_models/IRL_based_models/IRL_SVOpolicy_multi_rnn_ais_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+"_"+str(self.n_state_dec)+text+".pth"
            name_gen_path="trained_models/IRL_based_models/IRL_SVOpolicy_multi_rnn_ais_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+"_"+str(self.n_state_dec)+text+".pth"

        torch.save(self.gen_model.state_dict(),name_gen_path)
        torch.save(self.pred_model.state_dict(),name_pred_path)

        return "saved"
    
    def load_model_weights(self,text="_"):
        #name_gen_path="trained_models/IRL_based_models/IRL_SVOpolicy_ais_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+text+".pth"
        #torch.save(self.gen_model.state_dict(),name_gen_path)
        #self.gen_model.load_state_dict(torch.load(name_gen_path))
        #self.gen_model.eval()

        name_gen_path="_"
        name_pred_path="_"
        
        if self.ais_pred_model==1:
            name_pred_path="trained_models/IRL_based_models/IRL_SVOpolicy_ais_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+text+".pth"
            name_gen_path="trained_models/IRL_based_models/IRL_SVOpolicy_ais_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+text+".pth"

        if self.ais_pred_model==2:
            name_pred_path="trained_models/IRL_based_models/IRL_SVOpolicy_multi_rnn_ais_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+"_"+str(self.n_state_dec)+text+".pth"
            name_gen_path="trained_models/IRL_based_models/IRL_SVOpolicy_multi_rnn_ais_gen"+str(self.ais_gen_model)+"_"+str(self.n_psi2_in)+str(self.n_psi2_out)+"_pred"+str(self.ais_pred_model)+"_"+str(self.n_phi2_in)+str(self.n_phi2_out)+"_epochs"+str(self.n_epochs)+"_learning_rate"+str(self.learning_rate)+"_hidden_states"+str(self.n_state_enc)+"_"+str(self.n_state_dec)+text+".pth"
        
        #torch.save(self.pred_model.state_dict(),name_pred_path)
        self.gen_model.load_state_dict(torch.load(name_gen_path))
        self.gen_model.eval()

        self.pred_model.load_state_dict(torch.load(name_pred_path))
        self.pred_model.eval()

        return "loaded"
    

    def train(self):
        train_bar=pyprind.ProgBar(self.n_epochs)
        #self.optimizer_enc = torch.optim.Adam(list(self.gen_model.parameters()) + list(self.pred_model.parameters()), lr=self.learning_rate, amsgrad=True)
        #self.optimizer_dec = torch.optim.Adam(list(self.pred_model.parameters()), lr=self.learning_rate, amsgrad=True)
        self.optimizer = torch.optim.Adam(list(self.gen_model.parameters()) + list(self.pred_model.parameters()), lr=self.learning_rate, amsgrad=True)
        #self.optimizer_encoder=torch.optim.Adam(self.gen_model.parameters(), lr=self.learning_rate, amsgrad=True)
        #self.optimizer_decoder=torch.optim.Adam(self.pred_model.parameters(), lr=self.learning_rate, amsgrad=True)

        time_step_loss=0
        for epoch in range(self.n_epochs):

            train_bar.update()
            #keys_training=sample(keys_for_training,len(keys_for_training)) #shuffle the keys
            #train_bar=pyprind.ProgBar(len(keys_for_training))
            epoch_loss=0
            #for key in keys_training:
            for key in keys_for_testing[0]:
                #train_bar.update()
                key=str(key)                
                ############# Create the data for the training locally- we are restricting the number of timesteps to num_timesteps######
                negative_vals=[]
                for i in [0,1]:
                    negative_vals.append(list(filter(lambda x: x < 1, data_irl[key][i])))
                num_timesteps=min(self.min_timesteps,len(negative_vals[0]),len(negative_vals[1]))

                # Ais initialization
                time_step_loss=0

                ais_rollout_enc=0.5*torch.ones(self.n_state_enc,dtype=torch.float).to(self.device)
                state_rollout_enc=0.5*torch.ones(self.n_state_enc,dtype=torch.float).to(self.device)
                action_list=[0,0] ## initialize the action list differently                

                    
                for time_step in [0,10]:#range(10):                    
                    observation_list=[]
                    for i in range(len(data_irl[key])-2): # exclude the last two columns (actions/inputs)
                        temp=data_irl[key][i][time_step]
                        if temp!= None:
                            observation_list.append(temp)
                        
                    input_list=[]
                    input_list.extend(observation_list)
                    input_list.extend(action_list)
                    input_tensor=1*torch.tensor(input_list,dtype=torch.float).to(self.device)
                    '''
                    print("\n")
                    print("Before rollout, the input is ",input_tensor)
                    '''

                    # Update action list for the next time step and for the reference
                    for i in [4,5]:
                        temp=data_irl[key][i][time_step]
                        if temp!= None:
                            action_list[i-4]=temp
                        else:
                            action_list[i-4]=0

                    reference_list=[]
                    '''
                    observation_list_ref=[]
                    for i in [1,3]:#range(len(data_irl[key])-2): # exclude the last two columns (actions/inputs)
                        temp=data_irl[key][i][time_step+1]
                        if temp!= None:
                            observation_list_ref.append(temp)                      
                    reference_list.extend(observation_list_ref)

                    reference_list.extend([action_list[1]])
                    '''
                    observation_list_ref=[]
                    for i in [1]:#range(len(data_irl[key])-2): # exclude the last two columns (actions/inputs)
                        temp=data_irl[key][i][time_step+1]
                        if temp!= None:
                            observation_list_ref.append(temp)                      
                    reference_list.extend(observation_list_ref)
                    
                    reference_tensor=1*torch.tensor(reference_list,dtype=torch.float).to(self.device)

                    #############################
                    # Setting things up for the rollout
                    ais_rollout_dec=0.5*torch.ones(self.n_state_dec,dtype=torch.float).to(self.device) # Just initialize it to 0.5             
                    state_rollout_dec=0.5*torch.ones(self.n_state_dec,dtype=torch.float).to(self.device) # Just initialize it to 0.5             
                    

                    ## Setting internal rollout horizon
                    #internal_rollout_horizon=min(self.rollout,len(data_irl[key][0])-time_step-2)
                    internal_rollout_horizon=1
                    rollout_loss=0
                   
                    for k in range(internal_rollout_horizon):

                        if k==0:
                            #rollout_reference=0.5*torch.ones(self.n_output,dtype=torch.float).to(self.device)                           
                            rollout_input=input_tensor
                            rollout_reference=reference_tensor
                            rollout_reference.requires_grad_()
                            
                            print("for rollout",k,"encoder input is ",input_tensor,"hidden state:",ais_rollout_enc)
                            
                            #ais_rollout_enc=ais
                            #print("for rollout",k,"ais ",ais_rollout_enc)
                            ## GRU
                            #ais_rollout_enc=self.gen_model(rollout_input,ais_rollout_enc)
                            
                            ## LSTM
                            ais_rollout_enc,state_rollout_enc=self.gen_model(rollout_input,ais_rollout_enc,state_rollout_enc)
                            
                            print("for rollout",k,"updated hidden state:",ais_rollout_enc)
                            #ais=ais_rollout_enc

                            time_step_tensor=torch.tensor([time_step+k],dtype=torch.float).to(self.device)
                            decoder_input_tensor=torch.cat((ais_rollout_enc,time_step_tensor),0)

                            ## GRU
                            #rollout_prediction,ais_rollout_dec=self.pred_model(decoder_input_tensor,ais_rollout_dec)
                            ## LSTM
                            ais_rollout_dec,state_rollout_dec=self.pred_model(decoder_input_tensor,ais_rollout_dec,state_rollout_dec)
                            rollout_prediction=ais_rollout_dec
                            ## Linear
                            #rollout_prediction=self.pred_model(ais_rollout_enc)

                            #print("ais_rollout_dec",ais_rollout_dec.is_leaf)

                            print("for rollout",k,"decoder_input  is ",decoder_input_tensor)
                            print("for rollout",k,"rollout_prediction is ",rollout_prediction)
                            print("for rollout",k,"rollout_reference is ",rollout_reference,"\n")
                            '''
                            print("for rollout",k,"decoder_input  is ",decoder_input_tensor)
                            print("for rollout",k,"rollout_prediction is ",rollout_prediction)
                            '''
                            #### LOg likelihood loss
                            time_step_loss+=-torch.distributions.MultivariateNormal(rollout_prediction,torch.eye(rollout_prediction.shape[0]).to(self.device)).log_prob(rollout_reference)
                            
                            #loss_pred += -torch.distributions.MultivariateNormal(obs_pred_next_probs[0,:], torch.eye(obs_pred_next_probs[0,:].shape[0]).to(device)).log_prob(obs[step+1,:])

                            #print(time_step_loss)
                            #### RMS loss  
                            #time_step_loss+=torch.nn.functional.mse_loss(rollout_reference,rollout_prediction)
                            ### NLL loss
                            #rollout_loss+=torch.nn.functional.nll_loss(torch.relu(-rollout_prediction),torch.relu(-rollout_reference))     
                            #rollout_loss+=torch.nn.functional.nll_loss(rollout_prediction.view(1,-1),rollout_reference.view(1,-1))
                            #rollout_loss+=torch.nn.functional.nll_loss(torch.nn.functional.log_softmax(rollout_prediction),torch.nn.functional.log_softmax(rollout_reference))
                            #key_loss+=-torch.distributions.MultivariateNormal(rollout_prediction,torch.eye(rollout_prediction.shape[0]).to(self.device)).log_prob(rollout_reference)

                        else:
                            rollout_reference_list=[]
                            rollout_reference=0.5*torch.ones(self.n_output,dtype=torch.float).to(self.device)                           
                            for i in [1,3,5]:#range(len(data_irl[key])):
                                if i<4:
                                    rollout_reference_list.append(data_irl[key][i][time_step+k+1])
                                elif i>=4 and data_irl[key][i][time_step+k]!=None: # Previous action is observed at time_step+k+1
                                    rollout_reference_list.append(data_irl[key][i][time_step+k])
                                else:
                                    rollout_reference_list.append(0) # Zero padding for the input action

                            rollout_reference=torch.tensor(rollout_reference_list,dtype=torch.float).to(self.device)
                            rollout_reference.requires_grad_()
                            '''
                            print("for rollout",k,"rollout_reference is ",rollout_reference)
                            '''

                            time_step_tensor=torch.tensor([time_step+k],dtype=torch.float).to(self.device)
                            decoder_input_tensor=torch.cat((ais_rollout_enc,time_step_tensor),0)

                            ## GRU
                            #rollout_prediction,ais_rollout_dec=self.pred_model(decoder_input_tensor,ais_rollout_dec)
                            ## LSTM
                            rollout_prediction,ais_rollout_dec,state_rollout_dec=self.pred_model(decoder_input_tensor,ais_rollout_dec,state_rollout_dec)
                            ## Linear
                            #rollout_prediction=self.pred_model(ais_rollout_enc)
                            print("for rollout",k,"rollout_prediction is ",rollout_prediction)
                            print("for rollout",k,"rollout_reference is ",rollout_reference,"\n")

                            '''
                            print("for rollout",k,"decoder_input  is ",decoder_input_tensor)
                            print("for rollout",k,"rollout_prediction is ",rollout_prediction)
                            '''

                            #### LOg likelihood loss
                            time_step_loss+=-torch.distributions.MultivariateNormal(rollout_prediction,torch.eye(rollout_prediction.shape[0]).to(self.device)).log_prob(rollout_reference)

                            #### RMS loss  
                            #time_step_loss+=torch.nn.functional.mse_loss(rollout_reference,rollout_prediction)
                            ### NLL loss
                            #rollout_loss+=torch.nn.functional.nll_loss(torch.relu(-rollout_prediction),torch.relu(-rollout_reference)) 
                            #rollout_loss+=torch.nn.functional.nll_loss(rollout_prediction.view(1,-1),rollout_reference.view(1,-1))
                            #rollout_loss+=torch.nn.functional.nll_loss(torch.nn.functional.log_softmax(rollout_prediction),torch.nn.functional.log_softmax(rollout_reference))


                    #time_step_loss+=rollout_loss

                    '''
                    self.optimizer_dec.zero_grad()
                    rollout_loss.backward()
                    self.optimizer_dec.step()
                    '''
                    
                    
                
                self.optimizer.zero_grad()
                #self.optimizer_encoder.zero_grad()
                #self.optimizer_decoder.zero_grad()
                time_step_loss.backward()

                
                ## Printing the gradients
                print("Printing the gradients-encoder")
                print(self.gen_model.PSI_layer1.weight_ih.grad)
                print(self.gen_model.PSI_layer1.weight_hh.grad)
                print(self.gen_model.PSI_layer1.bias_ih.grad)
                print(self.gen_model.PSI_layer1.bias_hh.grad)
                
                '''
                #For non shallow encoder
                print(self.gen_model.PSI_layer2.weight_ih.grad)
                print(self.gen_model.PSI_layer2.weight_hh.grad)
                print(self.gen_model.PSI_layer2.bias_ih.grad)
                print(self.gen_model.PSI_layer2.bias_hh.grad)
                '''
                print("Printing the gradients-decoder")
                
                print(self.pred_model.PHI_layer1.weight_ih.grad)
                print(self.pred_model.PHI_layer1.weight_hh.grad)
                print(self.pred_model.PHI_layer1.bias_ih.grad)
                print(self.pred_model.PHI_layer1.bias_hh.grad)
                '''
                #For non shallow decoder
                print(self.pred_model.PHI_layer2.weight_ih.grad)
                print(self.pred_model.PHI_layer2.weight_hh.grad)
                print(self.pred_model.PHI_layer2.bias_ih.grad)
                print(self.pred_model.PHI_layer2.bias_hh.grad)
                '''
                '''
                print(self.pred_model.PHI_layer1.weight.grad)
                print(self.pred_model.PHI_layer2.weight.grad)
                print(self.pred_model.PHI_layer3.weight.grad)
                #print(self.pred_model.PHI_layer2.bias.grad)
                '''
                ##
                epoch_loss+=time_step_loss                
                self.optimizer.step()
                #self.optimizer_encoder.step()
                #self.optimizer_decoder.step()

                #self.optimizer_enc.zero_grad()
                #key_loss.backward()
                #self.optimizer_enc.step()
                #print("saving model weights")
                #status=self.save_model_weights("Rollout_10")
            print("epoch_loss is ",epoch_loss,"\n")                
            print("saving model weights for epoch ",epoch)
            status=self.save_model_weights("reduced_timesteps15_Rollout_1_added_time_step_to_decoder_input_minusall_magerr100")



    def test(self,test_keys):
        test_bar=pyprind.ProgBar(len(test_keys))
        self.comparision_list=[]
        #self.load_model_weights("Rollout_10")
        #print("loaded model weights")
            
        self.test_run_comparision=[]
        for test_run in range(len(test_keys)):
            test_bar.update()
            #key_test=str(test_keys[test_run])
            #key_test=str(keys_for_training[test_run])
            key_test=keys_for_training[0]
            
            ############# locally restrict the data for the training - we are restricting the number of timesteps to num_timesteps######
            negative_vals=[]
            for i in [0,1]:
                negative_vals.append(list(filter(lambda x: x < 1, data_irl[key_test][i])))

            num_timesteps=min(self.min_timesteps,len(negative_vals[0]),len(negative_vals[1]))
            
            # Ais initialization
            time_step_loss=0
            ais_rollout_enc=0.5*torch.ones(self.n_state_enc,dtype=torch.float).to(self.device)
            action_list=[0,0]             

            time_step_comparision=[]
            for time_step in range(num_timesteps):                    
                observation_list=[]
                for i in range(len(data_irl[key_test])-2): # exclude the last two columns (actions/inputs)
                    temp=data_irl[key_test][i][time_step]
                    if temp!= None:
                        observation_list.append(temp)
                    
                input_list=[]
                input_list.extend(observation_list)
                input_list.extend(action_list)
                input_tensor=torch.tensor(input_list,dtype=torch.float).to(self.device)
                print("\n")
                print("Before rollout, the input is ",input_tensor)
                # Update action list for the next time step and for the reference
                for i in [4,5]:
                    temp=data_irl[key_test][i][time_step]
                    if temp!= None:
                        action_list[i-4]=temp
                    else:
                        action_list[i-4]=0

                reference_list=[]
                observation_list_ref=[]
                for i in [1,3]:#range(len(data_irl[key_test])-2): # exclude the last two columns (actions/inputs)
                    temp=data_irl[key_test][i][time_step+1]
                    if temp!= None:
                        observation_list_ref.append(temp)                      
                reference_list.extend(observation_list_ref)
                reference_list.extend([action_list[1]])

                reference_tensor=1*torch.tensor(reference_list,dtype=torch.float).to(self.device)

                ais_rollout_dec=0.5*torch.ones(self.n_state_dec,dtype=torch.float).to(self.device) # Just initialize it to 0.5


                rollout_reference=0.5*torch.ones(self.n_output,dtype=torch.float).to(self.device)

                rollout_prediction=0.5*torch.ones(self.n_output,dtype=torch.float).to(self.device)

                #internal_rollout_horizon=min(self.rollout,len(data_irl[key_test][0])-time_step-2)
                internal_rollout_horizon=1
                rollout_loss=0

                rollout_comparison=[]
                for k in range(internal_rollout_horizon):
                    temp_comparision=[]
                    
                    #print("\n")
                    if k==0:
                        rollout_input=input_tensor
                        rollout_reference=reference_tensor
                        #ais_rollout_enc=ais
                        print("for rollout",k,"ais ",ais_rollout_enc)

                        ais_rollout_enc=self.gen_model(rollout_input,ais_rollout_enc)
                        #ais=ais_rollout_enc
                        
                        #decoder_input=list(ais_rollout_enc.detach().cpu().numpy())
                        #decoder_input.extend([time_step+k])
                        #decoder_input_tensor=torch.tensor(decoder_input,dtype=torch.float).to(self.device)
                        
                        time_step_tensor=torch.tensor([time_step+k],dtype=torch.float).to(self.device)
                        decoder_input_tensor=torch.cat((ais_rollout_enc,time_step_tensor),0)
                        rollout_prediction,ais_rollout_dec=self.pred_model(decoder_input_tensor,ais_rollout_dec)
                        
                        print("for rollout",k,"rollout_reference is ",rollout_reference)
                        print("for rollout",k,"decoder_input  is ",decoder_input_tensor,time_step+k)
                        print("for rollout",k,"rollout_prediction is ",rollout_prediction)
                        
                        rollout_loss+=-torch.distributions.MultivariateNormal(rollout_prediction,torch.eye(rollout_prediction.shape[0]).to(self.device)).log_prob(rollout_reference)

                        temp_comparision.extend(rollout_reference.detach().cpu().numpy())
                        temp_comparision.extend(rollout_prediction.detach().cpu().numpy())

                    else:
                        rollout_reference_list=[]                           
                        for i in [1,3,5]:#range(len(data_irl[key_test])):
                            if i<4:
                                rollout_reference_list.append(data_irl[key_test][i][time_step+k+1])
                            elif i>=4 and data_irl[key_test][i][time_step+k]!=None: # Previous action is observed at time_step+k+1
                                rollout_reference_list.append(data_irl[key_test][i][time_step+k])
                            else:
                                rollout_reference_list.append(0) # Zero padding for the input action

                        rollout_reference=1*torch.tensor(rollout_reference_list,dtype=torch.float).to(self.device)

                        
                        #decoder_input=list(ais_rollout_enc.detach().cpu().numpy())
                        #decoder_input.extend([time_step+k])
                        #decoder_input_tensor=torch.tensor(decoder_input,dtype=torch.float).to(self.device)

                        time_step_tensor=torch.tensor([time_step+k],dtype=torch.float).to(self.device)
                        decoder_input_tensor=torch.cat((ais_rollout_enc,time_step_tensor),0)
                        rollout_prediction,ais_rollout_dec=self.pred_model(decoder_input_tensor,ais_rollout_dec)                                                
                        
                        print("for rollout",k,"rollout_reference is ",rollout_reference)
                        print("for rollout",k,"decoder_input  is ",decoder_input_tensor,time_step+k)
                        print("for rollout",k,"rollout_prediction is ",rollout_prediction)

                        temp_comparision.extend(rollout_reference.detach().cpu().numpy())
                        temp_comparision.extend(rollout_prediction.detach().cpu().numpy())
                        rollout_loss+=-torch.distributions.MultivariateNormal(rollout_prediction,torch.eye(rollout_prediction.shape[0]).to(self.device)).log_prob(rollout_reference)
                    rollout_comparison.append(temp_comparision)
                time_step_comparision.append(rollout_comparison)    
            self.test_run_comparision.extend(time_step_comparision)
    
        return self

In [190]:
####### Parameters #######
n_epochs=2000
#min_timesteps=20
#n_rollout=10
#n_state_enc =24
#n_state_dec =12
min_timesteps=15
n_rollout=5
n_test=1
n_input=6
#n_output=3
n_output=1
#n_state_enc =4
#n_state_dec =5
n_state_enc =2
#n_state_dec =3
n_state_dec =1 # For shallow network pred
learning_rate=0.3
gen_model=2
pred_model=2
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [194]:
####### Initialise the neural network #######

network=NN_structure(n_epochs,min_timesteps,n_rollout,n_test,n_input,n_output,n_state_enc,n_state_dec,learning_rate,gen_model,pred_model,device)
print("Training has started")
network.train()


Training has started
for rollout 0 encoder input is  tensor([-50.0000, -56.3009,  10.0000,   8.0022,   0.0000,   0.0000],
       device='cuda:0') hidden state: tensor([0.5000, 0.5000], device='cuda:0')
Encoder Forward
for rollout 0 updated hidden state: tensor([-4.7148e-01,  2.5989e-04], device='cuda:0', grad_fn=<SqueezeBackward1>)
for rollout 0 decoder_input  is  tensor([-4.7148e-01,  2.5989e-04,  0.0000e+00], device='cuda:0',
       grad_fn=<CatBackward0>)
for rollout 0 rollout_prediction is  tensor([0.0103], device='cuda:0', grad_fn=<SqueezeBackward1>)
for rollout 0 rollout_reference is  tensor([-54.7269], device='cuda:0', requires_grad=True) 

for rollout 0 encoder input is  tensor([-31.8385, -43.1462,   9.8210,   4.9880,  -5.0000,  -1.3207],
       device='cuda:0') hidden state: tensor([-4.7148e-01,  2.5989e-04], device='cuda:0', grad_fn=<SqueezeBackward1>)
Encoder Forward
for rollout 0 updated hidden state: tensor([-2.7181e-03,  4.8192e-07], device='cuda:0', grad_fn=<SqueezeBackw

0% [#                             ] 100% | ETA: 00:02:13

for rollout 0 encoder input is  tensor([-31.8385, -43.1462,   9.8210,   4.9880,  -5.0000,  -1.3207],
       device='cuda:0') hidden state: tensor([0.0000, 0.9051], device='cuda:0', grad_fn=<SqueezeBackward1>)
Encoder Forward
for rollout 0 updated hidden state: tensor([0.0000, 0.9866], device='cuda:0', grad_fn=<SqueezeBackward1>)
for rollout 0 decoder_input  is  tensor([ 0.0000,  0.9866, 10.0000], device='cuda:0', grad_fn=<CatBackward0>)
for rollout 0 rollout_prediction is  tensor([-0.7616], device='cuda:0', grad_fn=<SqueezeBackward1>)
for rollout 0 rollout_reference is  tensor([-42.1858], device='cuda:0', requires_grad=True) 

Printing the gradients-encoder
tensor([[0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.]], device='cuda:0')
tensor([[0., 0.],
        [0., 0.],
        

0% [##                            ] 100% | ETA: 00:02:00

tensor([0.0000, 0.9051, 0.0000], device='cuda:0', grad_fn=<CatBackward0>)
for rollout 0 rollout_prediction is  tensor([-0.7616], device='cuda:0', grad_fn=<SqueezeBackward1>)
for rollout 0 rollout_reference is  tensor([-54.7269], device='cuda:0', requires_grad=True) 

for rollout 0 encoder input is  tensor([-31.8385, -43.1462,   9.8210,   4.9880,  -5.0000,  -1.3207],
       device='cuda:0') hidden state: tensor([0.0000, 0.9051], device='cuda:0', grad_fn=<SqueezeBackward1>)
Encoder Forward
for rollout 0 updated hidden state: tensor([0.0000, 0.9866], device='cuda:0', grad_fn=<SqueezeBackward1>)
for rollout 0 decoder_input  is  tensor([ 0.0000,  0.9866, 10.0000], device='cuda:0', grad_fn=<CatBackward0>)
for rollout 0 rollout_prediction is  tensor([-0.7616], device='cuda:0', grad_fn=<SqueezeBackward1>)
for rollout 0 rollout_reference is  tensor([-42.1858], device='cuda:0', requires_grad=True) 

Printing the gradients-encoder
tensor([[0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.]

...

0% [#######################       ] 100% | ETA: 00:00:31

tensor([[0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0.]], device='cuda:0')
tensor([[0., 0.],
        [0., 0.],
        [0., 0.],
        [0., 0.],
        [0., 0.],
        [0., 0.],
        [0., 0.],
        [0., 0.]], device='cuda:0')
tensor([0., 0., 0., 0., 0., 0., 0., 0.], device='cuda:0')
tensor([0., 0., 0., 0., 0., 0., 0., 0.], device='cuda:0')
Printing the gradients-decoder
tensor([[ 0.0000e+00, -1.1005e-04,  0.0000e+00],
        [ 0.0000e+00,  5.4381e-05,  4.4466e-15],
        [ 0.0000e+00,  4.8910e-06,  0.0000e+00],
        [ 0.0000e+00, -1.3748e-04,  0.0000e+00]], device='cuda:0')
tensor([[-6.0790e-05],
        [ 3.0040e-05],
        [ 2.7018e-06],
        [-7.5941e-05]], device='cuda:0')
tensor([-1.2158e-04,  6.0079e-05,  5.4035e-06, -1.5188e-04], device='cuda:0')

0% [########################      ] 100% | ETA: 00:00:26

for rollout 0 encoder input is  tensor([-50.0000, -56.3009,  10.0000,   8.0022,   0.0000,   0.0000],
       device='cuda:0') hidden state: tensor([0.5000, 0.5000], device='cuda:0')
Encoder Forward
for rollout 0 updated hidden state: tensor([0.0000, 0.9051], device='cuda:0', grad_fn=<SqueezeBackward1>)
for rollout 0 decoder_input  is  tensor([0.0000, 0.9051, 0.0000], device='cuda:0', grad_fn=<CatBackward0>)
for rollout 0 rollout_prediction is  tensor([-0.7616], device='cuda:0', grad_fn=<SqueezeBackward1>)
for rollout 0 rollout_reference is  tensor([-54.7269], device='cuda:0', requires_grad=True) 

for rollout 0 encoder input is  tensor([-31.8385, -43.1462,   9.8210,   4.9880,  -5.0000,  -1.3207],
       device='cuda:0') hidden state: tensor([0.0000, 0.9051], device='cuda:0', grad_fn=<SqueezeBackward1>)
Encoder Forward
for rollout 0 updated hidden state: tensor([0.0000, 0.9866], device='cuda:0', grad_fn=<SqueezeBackward1>)
for rollout 0 decoder_input  is  tensor([ 0.0000,  0.9866, 10.000

KeyboardInterrupt: 

In [229]:
# Test the network

####### Load the neural network weights from saved models #######

loaded_network=NN_structure(n_epochs,min_timesteps,n_rollout,n_test,n_input,n_output,n_state_enc,n_state_dec,learning_rate,gen_model,pred_model,device)
loaded_network.load_model_weights("reduced_timesteps15_Rollout_1_added_time_step_to_decoder_input_minusall_magerr100")


test_keys=[keys_for_testing[15]]
test_results=loaded_network.test(test_keys)

0% [#] 100% | ETA: 00:00:00
Total time elapsed: 00:00:00




Before rollout, the input is  tensor([-50.0000, -50.1345,  10.0000,   5.3078,   0.0000,   0.0000],
       device='cuda:0')
for rollout 0 ais  tensor([0.5000, 0.5000], device='cuda:0')
for rollout 0 rollout_reference is  tensor([-4.9073e+01,  5.3081e+00,  1.8404e-03], device='cuda:0')
for rollout 0 decoder_input  is  tensor([1., 1., 0.], device='cuda:0', grad_fn=<CatBackward0>) 0
for rollout 0 rollout_prediction is  tensor([-0.0000, -0.0000, -1.3220], device='cuda:0', grad_fn=<NegBackward0>)


Before rollout, the input is  tensor([-4.8100e+01, -4.9073e+01,  9.0000e+00,  5.3081e+00, -5.0000e+00,
         1.8404e-03], device='cuda:0')
for rollout 0 ais  tensor([1., 1.], device='cuda:0', grad_fn=<SqueezeBackward1>)
for rollout 0 rollout_reference is  tensor([-4.8011e+01,  5.3085e+00,  1.6556e-03], device='cuda:0')
for rollout 0 decoder_input  is  tensor([1., 1., 1.], device='cuda:0', grad_fn=<CatBackward0>) 1
for rollout 0 rollout_prediction is  tensor([-0.0000, -0.0000, -1.3517], device

In [214]:
test_results.test_run_comparision

[[[-49.07296, 5.3081274, 0.0018403638, -18.169144, 5.5449357, -1.6968961]],
 [[-48.011303, 5.3084583, 0.0016555589, -18.171122, 5.5455713, -1.6971188]],
 [[-46.94958, 5.3087554, 0.0014832187, -18.171967, 5.545838, -1.6972182]],
 [[-45.887806, 5.3090115, 0.0012823439, -18.172344, 5.545954, -1.697264]],
 [[-44.82598, 5.3092246, 0.0010645859, -18.17252, 5.5460067, -1.6972859]],
 [[-43.76412, 5.3093905, 0.00082904915, -18.172604, 5.5460324, -1.6972971]],
 [[-42.70223, 5.3095055, 0.00057430426, -18.172646, 5.5460453, -1.6973026]],
 [[-41.640324, 5.309565, 0.00029867006, -18.172668, 5.546051, -1.6973054]],
 [[-40.57841, 5.309565, 1.7601678e-07, -18.17268, 5.5460544, -1.6973069]],
 [[-39.516502, 5.3095, -0.0003234884, -18.172684, 5.546056, -1.6973078]],
 [[-38.454617, 5.3093653, -0.00067481643, -18.172688, 5.5460567, -1.6973081]],
 [[-37.392765, 5.309154, -0.0010562867, -18.17269, 5.5460577, -1.6973085]],
 [[-36.330963, 5.30886, -0.0014708722, -18.172688, 5.546057, -1.6973083]],
 [[-35.26923,

In [86]:
#print(len(test_results.test_run_comparision[0][1]))

#test_results.test_run_comparision[19][:]


# Plot the results only for the HDV
pos_t=[]
vel_t=[]
acc_t=[]
pos_tref=[]
vel_tref=[]
acc_tref=[]
pos_t_hdv=[]
vel_t_hdv=[]
acc_t_hdv=[]
pos_tref_hdv=[]
vel_tref_hdv=[]
acc_tref_hdv=[]

# set which timestep to plot
time_step=10

for index in range(len(test_results.test_run_comparision[time_step])):
    '''
    pos_tref.append(test_results.test_run_comparision[time_step][index][0])
    vel_tref.append(test_results.test_run_comparision[time_step][index][2])
    acc_tref.append(test_results.test_run_comparision[time_step][index][4])
    pos_t.append(test_results.test_run_comparision[time_step][index][6])
    vel_t.append(test_results.test_run_comparision[time_step][index][8])
    acc_t.append(test_results.test_run_comparision[time_step][index][10])
    
    #pos_t_hdv.append(test_results.test_run_comparision[time_step][index][1])
    #vel_t_hdv.append(test_results.test_run_comparision[time_step][index][3])
    #acc_t_hdv.append(test_results.test_run_comparision[time_step][index][5])
    #pos_tref_hdv.append(test_results.test_run_comparision[time_step][index][7])
    #vel_tref_hdv.append(test_results.test_run_comparision[time_step][index][9])
    #acc_tref_hdv.append(test_results.test_run_comparision[time_step][index][11])

    
    pos_tref_hdv.append(test_results.test_run_comparision[time_step][index][1])
    vel_tref_hdv.append(test_results.test_run_comparision[time_step][index][3])
    acc_tref_hdv.append(test_results.test_run_comparision[time_step][index][5])
    pos_t_hdv.append(test_results.test_run_comparision[time_step][index][7])
    vel_t_hdv.append(test_results.test_run_comparision[time_step][index][9])
    acc_t_hdv.append(test_results.test_run_comparision[time_step][index][11])
    '''

    pos_tref_hdv.append(test_results.test_run_comparision[time_step][index][0])
    vel_tref_hdv.append(test_results.test_run_comparision[time_step][index][1])
    acc_tref_hdv.append(test_results.test_run_comparision[time_step][index][2])
    pos_t_hdv.append(test_results.test_run_comparision[time_step][index][3])
    vel_t_hdv.append(test_results.test_run_comparision[time_step][index][4])
    acc_t_hdv.append(test_results.test_run_comparision[time_step][index][5])


IndexError: list index out of range

In [ ]:
plot_data=data_irl[str(keys_for_testing[10])]    

pos_t_hdv=[]
vel_t_hdv=[]
acc_t_hdv=[]
pos_tref_hdv=[]
vel_tref_hdv=[]
acc_tref_hdv=[]

    for index in range(len(plot_data[0])):

        pos_t_hdv.append(test_results.test_run_comparision[time_step][index][1].detach().cpu().numpy())
        vel_t_hdv.append(test_results.test_run_comparision[time_step][index][3].detach().cpu().numpy())
        acc_t_hdv.append(test_results.test_run_comparision[time_step][index][5].detach().cpu().numpy())
        pos_tref_hdv.append(test_results.test_run_comparision[time_step][index][7].detach().cpu().numpy())
        vel_tref_hdv.append(test_results.test_run_comparision[time_step][index][9].detach().cpu().numpy())
        acc_tref_hdv.append(test_results.test_run_comparision[time_step][index][11].detach().cpu().numpy())

In [29]:
# Plotting outputs #
import matplotlib.colors as mcolors
####### For X - lateral#########
fig, ax = plt.subplots()
#plt.plot(y_ref,x_ref,'r',linewidth=2.0,label="Actual")
#plt.plot(y_pred,x_pred,'b',linewidth=2.0,label="Predicted")
plt.figure(facecolor='white')
plt.plot(pos_t_hdv,mcolors.CSS4_COLORS['salmon'],linewidth=2.0,label="Actual")
plt.plot(pos_tref_hdv,mcolors.CSS4_COLORS['limegreen'],linewidth=2.0,label="Predicted")
plt.xlabel('Time in (1/10)s')
plt.ylabel('Position along the road m')
plt.title('Comparision_of_position_along_road')
plt.legend()
plt.grid()
plt.savefig('graphs/irl_graphs/Comparision_rollout10_timestep_min20_posref_pospred_g1_p2_lr0005.png')
plt.close()

fig, ax = plt.subplots()
plt.figure(facecolor='white')
plt.plot(vel_t_hdv,mcolors.CSS4_COLORS['salmon'],linewidth=2.0,label="Actual")
plt.plot(vel_tref_hdv,mcolors.CSS4_COLORS['limegreen'],linewidth=2.0,label="Predicted")
plt.xlabel('Time in (1/10)s')
plt.ylabel('Velocity along the road in m/s')
plt.title('Comparision_Lateral_Velocities')
plt.legend()
plt.grid()
plt.savefig('graphs/irl_graphs/Comparision_rollout10_timestep_min20_vref_vpre_g1_p2_lr0005.png')
plt.close()

In [78]:
test_results.test_run_comparision[1][0]
#len(test_results.test_run_comparision)

[tensor(-46.4000, device='cuda:0'),
 tensor(-53.2063, device='cuda:0'),
 tensor(8., device='cuda:0'),
 tensor(7.4680, device='cuda:0'),
 tensor(-5., device='cuda:0'),
 tensor(-1.3502, device='cuda:0'),
 tensor(-31.8437, device='cuda:0', grad_fn=<UnbindBackward0>),
 tensor(-27.8377, device='cuda:0', grad_fn=<UnbindBackward0>),
 tensor(4.1773, device='cuda:0', grad_fn=<UnbindBackward0>),
 tensor(9.0293, device='cuda:0', grad_fn=<UnbindBackward0>),
 tensor(-1.2700, device='cuda:0', grad_fn=<UnbindBackward0>),
 tensor(0.0087, device='cuda:0', grad_fn=<UnbindBackward0>)]

In [202]:
'''
input = torch.randn(3, 5, requires_grad=True)
# each element in target has to have 0 <= value < C
target = torch.tensor([1, 0, 4])
output = torch.nn.functional.nll_loss(torch.nn.LogSoftmax(input, dim=1), target)
output.backward()
'''
m = nn.LogSoftmax(dim=1)
input = torch.randn(2, 3)
output = m(input)

input = torch.randn(3, 5, requires_grad=True)
target = torch.tensor([1, 0, 4])
output2 = torch.nn.functional.nll_loss(m(input), target)
